In [1]:
import datetime as dt
import math

import matplotlib.pyplot as plt
import mplfinance as mpf
import numpy as np
import pandas as pd
import pandas_market_calendars as mcal
import plotly.graph_objects as go
import polars as pl
from dash import Dash, dcc, html
from plotly.subplots import make_subplots

nse = mcal.get_calendar("NSE")

pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)

pd.options.display.float_format = "{:.4f}".format

import sys

sys.path.append("..")
# from tooling.enums import AssetClass, Index, Spot, StrikeSpread
# from tooling.fetch import fetch_option_data, fetch_spot_data
# from tooling.filter import find_atm, option_tool

from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import (
    _fetch_batch,
    fetch_data,
    fetch_spot_data,
)

In [2]:
# bnf_pandas = pd.read_csv("../data/bnf_min.csv")
bnf_pandas = pd.read_csv("../data/ng_1hr.csv")
# bnf_pandas = pd.read_csv("../data/fin_min.csv")
# bnf_pandas = pd.read_csv("../data/midcp_min.csv")
# bnf_pandas = pd.read_csv("../data/sensex_min.csv")
# bnf_pandas = pd.read_csv("../data/bankex_min.csv")

In [3]:
# If Stocks Data ...
bnf_pandas["time"] = pd.to_datetime(bnf_pandas["time"])
bnf_pandas["time"] = bnf_pandas["time"].dt.tz_localize(None)
bnf_pandas = bnf_pandas[bnf_pandas["time"].dt.year >= 2017]
bnf_pandas['datetime'] = bnf_pandas['time']
bnf_pandas.drop(columns=["time"], inplace=True)
# bnf_pandas

In [4]:
bnf = pl.DataFrame(bnf_pandas)
print(type(bnf))
# bnf

<class 'polars.dataframe.frame.DataFrame'>


In [5]:
bnf = bnf.with_columns([pl.col("datetime").alias("index")]).drop("datetime")
bnf = bnf.with_columns(pl.col("index").alias("datetime"))

In [6]:
bnf = bnf.rename({"open": "o", "high": "h", "low": "l", "close": "c"})

In [7]:
bnf.tail()

shape: (5, 6)
┌───────┬───────┬───────┬───────┬─────────────────────┬─────────────────────┐
│ o     ┆ h     ┆ l     ┆ c     ┆ index               ┆ datetime            │
│ ---   ┆ ---   ┆ ---   ┆ ---   ┆ ---                 ┆ ---                 │
│ f64   ┆ f64   ┆ f64   ┆ f64   ┆ datetime[ns]        ┆ datetime[ns]        │
╞═══════╪═══════╪═══════╪═══════╪═════════════════════╪═════════════════════╡
│ 324.2 ┆ 329.8 ┆ 323.1 ┆ 327.0 ┆ 2024-12-24 20:00:00 ┆ 2024-12-24 20:00:00 │
│ 327.0 ┆ 332.5 ┆ 327.0 ┆ 331.4 ┆ 2024-12-24 21:00:00 ┆ 2024-12-24 21:00:00 │
│ 331.3 ┆ 332.8 ┆ 326.6 ┆ 332.4 ┆ 2024-12-24 22:00:00 ┆ 2024-12-24 22:00:00 │
│ 332.2 ┆ 336.9 ┆ 329.6 ┆ 334.1 ┆ 2024-12-24 23:00:00 ┆ 2024-12-24 23:00:00 │
│ 328.9 ┆ 328.9 ┆ 327.3 ┆ 327.7 ┆ 2024-12-26 09:00:00 ┆ 2024-12-26 09:00:00 │
└───────┴───────┴───────┴───────┴─────────────────────┴─────────────────────┘

In [11]:
def trade(df, x=0.02, y=0.01):
    # Ensure datetime column is in the correct format
    df['datetime'] = pd.to_datetime(df['datetime'])

    # Set datetime as the index for time-based operations
    df = df.set_index('datetime')

    # Create a date column for grouping
    df['date'] = df.index.date

    # Calculate daily range (high - low) for each day between 9 AM and 3 PM
    intraday_df = df.between_time("09:00", "15:00")
    daily_range = intraday_df.groupby('date').agg({'h': 'max', 'l': 'min'})
    daily_range['range'] = daily_range['h'] - daily_range['l']

    # Initialize tradebook
    tradebook = []

    # Iterate over days to simulate trades
    for date, data in df.groupby('date'):
        if len(data) < 2:
            continue  # Skip if insufficient data

        # Extract 4 PM open price
        open_price_4pm = data.between_time("16:00", "16:00")['o']
        if open_price_4pm.empty:
            continue

        open_price_4pm = open_price_4pm.iloc[0]
        day_high = daily_range.loc[date, 'h']
        day_low = daily_range.loc[date, 'l']
        day_range = daily_range.loc[date, 'range']
        long_entry_price = open_price_4pm + x * day_range
        short_entry_price = open_price_4pm - x * day_range

        # Find trades after 4 PM
        trades = data[data.index > pd.to_datetime(f"{date} 16:00:00")]

        # Get the last candle of the day
        last_candle = trades.iloc[-1] if not trades.empty else None

        # Track active trades
        active_long = False
        active_short = False

        take_exit_long = False
        take_exit_short = False

        for idx, row in trades.iterrows():
            # entry_time = idx

            # Check for long entry
            if not active_long and row['h'] >= long_entry_price:
                active_long = True
                sl = long_entry_price - y * day_range
                target = long_entry_price + 2 * y * day_range
                entry_time = idx

            if active_long:
                # Determine exit
                if row['l'] <= sl:  # Stop-loss hit
                    exit_price = sl
                    exit_time = idx
                    take_exit_long = True
                    exit_remark_long = 'SL'
                elif row['h'] >= target:  # Target hit
                    exit_price = target
                    exit_time = idx
                    take_exit_long = True
                    exit_remark_long = 'Target'
                elif last_candle is not None:  # End of the day exit
                    exit_price = last_candle['c']
                    exit_time = last_candle.name
                    take_exit_long = True
                    exit_remark_long = 'EOD'
                else:
                    continue

                if take_exit_long:
                    points_captured = exit_price - long_entry_price
                    
                    tradebook.append({
                        'entry_time': entry_time,
                        'exit_time': exit_time,
                        'entry_price': long_entry_price,
                        'exit_price': exit_price,
                        'points_captured': points_captured,
                        'remark': exit_remark_long,
                        'trade_type': 'Long',
                        'day_high_till_3pm': day_high,
                        'day_low_till_3pm': day_low,
                        'day_range': day_range,
                    })
    
                    active_long = False  # Reset active trade after exit
                    take_exit_long = False

            # Check for short entry
            if not active_short and row['l'] <= short_entry_price:
                active_short = True
                sl = short_entry_price + y * day_range
                target = short_entry_price - 2 * y * day_range
                entry_time = idx

            if active_short:
                # Determine exit
                if row['h'] >= sl:  # Stop-loss hit
                    exit_price = sl
                    exit_time = idx
                    take_exit_short = True
                    exit_remark_short = 'SL'
                elif row['l'] <= target:  # Target hit
                    exit_price = target
                    exit_time = idx
                    take_exit_short = True
                    exit_remark_short = 'Target'
                elif last_candle is not None:  # End of the day exit
                    exit_price = last_candle['c']
                    exit_time = last_candle.name
                    take_exit_short = True
                    exit_remark_short = 'EOD'
                else:
                    continue

                if take_exit_short:
    
                    points_captured = short_entry_price - exit_price
    
                    tradebook.append({
                        'entry_time': entry_time,
                        'exit_time': exit_time,
                        'entry_price': short_entry_price,
                        'exit_price': exit_price,
                        'points_captured': points_captured,
                        'remark': exit_remark_short,
                        'trade_type': 'Short',
                        'day_high_till_3pm': day_high,
                        'day_low_till_3pm': day_low,
                        'day_range': day_range,
                    })
    
                    active_short = False  # Reset active trade after exit
                    take_exit_short = False

    # Create DataFrame for tradebook
    tradebook_df = pd.DataFrame(tradebook)
    return tradebook_df


In [12]:
data = bnf
df = pd.DataFrame(data)
df.columns = ['o', 'h', 'l', 'c', 'index', 'datetime']
tradebook = trade(df, x=0.02, y=0.01)
# print(tradebook)

In [13]:
tradebook

entry_time           exit_time  entry_price  exit_price  \
0    2020-12-28 17:00:00 2020-12-28 17:00:00     168.6260    168.3520   
1    2020-12-28 18:00:00 2020-12-28 18:00:00     168.6260    168.3520   
2    2020-12-28 19:00:00 2020-12-28 19:00:00     168.6260    168.3520   
3    2020-12-28 20:00:00 2020-12-28 20:00:00     168.6260    168.3520   
4    2020-12-28 21:00:00 2020-12-28 21:00:00     168.6260    168.3520   
5    2020-12-28 22:00:00 2020-12-28 22:00:00     169.1740    169.0370   
6    2020-12-28 22:00:00 2020-12-28 22:00:00     168.6260    168.7630   
7    2020-12-28 23:00:00 2020-12-28 23:00:00     169.1740    169.0370   
8    2020-12-28 23:00:00 2020-12-28 23:00:00     168.6260    168.7630   
9    2020-12-29 17:00:00 2020-12-29 17:00:00     172.4760    172.5520   
10   2020-12-29 18:00:00 2020-12-29 18:00:00     172.4760    172.5520   
11   2020-12-29 19:00:00 2020-12-29 19:00:00     172.4760    172.5520   
12   2020-12-29 20:00:00 2020-12-29 20:00:00     172.4760    172.5520   
13   2020-12-29 21:00:00 2020-12-29 21:00:00     172.4760    172.5520   
14   2020-12-29 22:00:00 2020-12-29 22:00:00     172.4760    172.5520   
15   2020-12-29 23:00:00 2020-12-29 23:00:00     172.4760    172.5520   
16   2020-12-30 17:00:00 2020-12-30 17:00:00     179.3540    179.3270   
17   2020-12-30 17:00:00 2020-12-30 17:00:00     179.2460    179.2730   
18   2020-12-30 18:00:00 2020-12-30 18:00:00     179.3540    179.4080   
19   2020-12-30 19:00:00 2020-12-30 19:00:00     179.3540    179.3270   
20   2020-12-30 19:00:00 2020-12-30 19:00:00     179.2460    179.2730   
21   2020-12-30 20:00:00 2020-12-30 20:00:00     179.3540    179.3270   
22   2020-12-30 20:00:00 2020-12-30 20:00:00     179.2460    179.2730   
23   2020-12-30 21:00:00 2020-12-30 21:00:00     179.3540    179.3270   
24   2020-12-30 21:00:00 2020-12-30 21:00:00     179.2460    179.2730   
25   2020-12-30 22:00:00 2020-12-30 22:00:00     179.2460    179.1920   
26   2020-12-30 23:00:00 2020-12-30 23:00:00     179.2460    179.1920   
27   2020-12-31 17:00:00 2020-12-31 17:00:00     183.6200    183.5600   
28   2020-12-31 17:00:00 2020-12-31 17:00:00     183.3800    183.4400   
29   2020-12-31 18:00:00 2020-12-31 18:00:00     183.6200    183.5600   
30   2020-12-31 18:00:00 2020-12-31 18:00:00     183.3800    183.4400   
31   2020-12-31 19:00:00 2020-12-31 19:00:00     183.3800    183.4400   
32   2020-12-31 20:00:00 2020-12-31 20:00:00     183.3800    183.2600   
33   2020-12-31 21:00:00 2020-12-31 21:00:00     183.3800    183.2600   
34   2020-12-31 22:00:00 2020-12-31 22:00:00     183.3800    183.2600   
35   2020-12-31 23:00:00 2020-12-31 23:00:00     183.3800    183.2600   
36   2021-01-04 17:00:00 2021-01-04 17:00:00     191.8900    191.8450   
37   2021-01-04 17:00:00 2021-01-04 17:00:00     191.7100    191.7550   
38   2021-01-04 18:00:00 2021-01-04 18:00:00     191.8900    191.8450   
39   2021-01-04 18:00:00 2021-01-04 18:00:00     191.7100    191.7550   
40   2021-01-04 19:00:00 2021-01-04 19:00:00     191.8900    191.9800   
41   2021-01-04 20:00:00 2021-01-04 20:00:00     191.8900    191.8450   
42   2021-01-04 20:00:00 2021-01-04 20:00:00     191.7100    191.7550   
43   2021-01-04 21:00:00 2021-01-04 21:00:00     191.8900    191.8450   
44   2021-01-04 21:00:00 2021-01-04 21:00:00     191.7100    191.7550   
45   2021-01-04 22:00:00 2021-01-04 22:00:00     191.7100    191.6200   
46   2021-01-04 23:00:00 2021-01-04 23:00:00     191.7100    191.6200   
47   2021-01-05 17:00:00 2021-01-05 17:00:00     197.7580    197.6790   
48   2021-01-05 17:00:00 2021-01-05 17:00:00     197.4420    197.5210   
49   2021-01-05 18:00:00 2021-01-05 18:00:00     197.7580    197.6790   
50   2021-01-05 18:00:00 2021-01-05 18:00:00     197.4420    197.5210   
51   2021-01-05 19:00:00 2021-01-05 19:00:00     197.7580    197.6790   
52   2021-01-05 19:00:00 2021-01-05 19:00:00     197.4420    197.5210   
53   2021-01-05 20:00:00 2021-01-05 20:00:00     197.7580    197.6790   